# Librerías

In [1]:
import pandas as pd
import numpy as np
import re
import nltk
import matplotlib.pyplot as plt

# Corpus etiquetado

In [2]:
etiquetas = ["dickens_a_christmas_carol",
             "dickens_a_tale_of_two_cities",
             "dickens_oliver_twist",
             "shakespeare_hamlet",
             "shakespeare_romeo_juliet",
             "shakespeare_the_merchant_of_venice"]
corpus = []

for etiqueta in etiquetas:
  archivo = open(etiqueta + ".txt", "r")
  corpus.append(archivo.read())
  archivo.close()


corpus = np.array(corpus)
df_corpus = pd.DataFrame({"documento": corpus,
                          "categoria": etiquetas})
df_corpus

documento  \
0  project,gutenberg,ebook,christmas,carol,charle...   
1  project,gutenberg,ebook,tale,two,city,charles,...   
2  project,gutenberg,ebook,oliver,twist,charles,d...   
3  project,gutenberg,ebook,hamlet,william,shakesp...   
4  project,gutenberg,ebook,romeo,juliet,william,s...   
5  project,gutenberg,ebook,merchant,venice,willia...   

                            categoria  
0           dickens_a_christmas_carol  
1        dickens_a_tale_of_two_cities  
2                dickens_oliver_twist  
3                  shakespeare_hamlet  
4            shakespeare_romeo_juliet  
5  shakespeare_the_merchant_of_venice

# Modelo de Bolsa de Palabras

In [3]:
from sklearn.feature_extraction.text import CountVectorizer
# bolsa de palabras en matriz dispersa
count_vectorizer = CountVectorizer(min_df=0.0, max_df=1.0)
matriz_conteo = count_vectorizer.fit_transform(corpus)
matriz_conteo

<Compressed Sparse Row sparse matrix of dtype 'int64'
	with 30424 stored elements and shape (6, 15164)>

In [4]:
# ver valores diferentes de cero en la matriz dispersa
print(matriz_conteo)

<Compressed Sparse Row sparse matrix of dtype 'int64'
	with 30424 stored elements and shape (6, 15164)>
  Coords	Values
  (0, 10315)	89
  (0, 6108)	95
  (0, 4317)	20
  (0, 2370)	97
  (0, 2094)	9
  (0, 2250)	5
  (0, 3735)	2
  (0, 2159)	1
  (0, 15082)	2
  (0, 1591)	1
  (0, 8214)	26
  (0, 13475)	19
  (0, 178)	2
  (0, 13227)	13
  (0, 567)	13
  (0, 7486)	2
  (0, 1710)	7
  (0, 6117)	1
  (0, 6118)	1
  (0, 6119)	1
  (0, 6120)	1
  (0, 6121)	1
  (0, 6122)	1
  (0, 2172)	14
  (0, 6283)	5
  :	:
  (5, 12639)	1
  (5, 4629)	1
  (5, 1976)	1
  (5, 15036)	1
  (5, 4513)	1
  (5, 1070)	1
  (5, 3253)	1
  (5, 13697)	1
  (5, 730)	1
  (5, 5710)	1
  (5, 10074)	2
  (5, 11587)	1
  (5, 1329)	5
  (5, 9004)	1
  (5, 15012)	1
  (5, 3920)	1
  (5, 4522)	1
  (5, 848)	1
  (5, 1303)	2
  (5, 8513)	1
  (5, 450)	1
  (5, 14086)	1
  (5, 8185)	1
  (5, 5686)	1
  (5, 5687)	1


In [5]:
# ver la representación densa
matriz_conteo = matriz_conteo.toarray()
matriz_conteo

array([[1, 1, 0, ..., 1, 0, 0],
       [1, 0, 0, ..., 1, 0, 0],
       [1, 0, 0, ..., 0, 0, 0],
       [3, 0, 1, ..., 2, 1, 0],
       [3, 0, 0, ..., 1, 0, 2],
       [1, 0, 0, ..., 0, 0, 0]])

In [6]:
# obten todas las palabras únicas del corpus
vocabulario = count_vectorizer.get_feature_names_out()
# muestra los vectores de características del documento
pd.DataFrame(matriz_conteo, columns=vocabulario)

000  00033  04  08  0em  10  100  101  102  103  ...  yourn  youth  \
0    1      1   0   0    0   2    2    1    1    1  ...      0      1   
1    1      0   0   0    0   2    0    0    0    0  ...      1     10   
2    1      0   0   0    2   0    0    0    0    0  ...      0      9   
3    3      0   1   0    0   2    3    0    0    0  ...      0     14   
4    3      0   0   1    0   2    1    0    0    0  ...      0      6   
5    1      0   0   0    2   0    0    0    0    0  ...      0      8   

   youthful  youthfulness  zeal  zealous  zenith  zip  zone  zounds  
0         0             0     1        0       0    1     0       0  
1         3             1     0        2       0    1     0       0  
2         6             0     0        2       1    0     0       0  
3         0             0     0        0       0    2     1       0  
4         3             0     0        0       0    1     0       2  
5         1             0     1        0       0    0     0       0  

[6 rows x 15164 columns]

#Vocabulario (número de columnas de la matriz)

In [7]:
print(len(vocabulario), vocabulario)

np.savetxt("vocab.txt", vocabulario, fmt="%s", delimiter=",")

15164 ['000' '00033' '04' ... 'zip' 'zone' 'zounds']


# Verificacion de resultado: baseline vs serial

In [ ]:
# Leer CSV generado por C++
df_csv = pd.read_csv("bolsa_serial.csv")

# Crear CountVectorizer de nuevo 
count_vectorizer = CountVectorizer(min_df=0.0, max_df=1.0)
matriz_conteo = count_vectorizer.fit_transform(df_corpus["documento"]).toarray()
vocabulario_sklearn = count_vectorizer.get_feature_names_out()

# Convertir la matriz sklearn a DataFrame con mismas etiquetas de documento
df_sklearn = pd.DataFrame(matriz_conteo, columns=vocabulario_sklearn)
df_sklearn.index = etiquetas

# Asegurar que las columnas estén ordenadas igual en ambos
csv_columns = df_csv.columns.tolist()
sklearn_columns = df_sklearn.columns.tolist()

if set(csv_columns) != set(sklearn_columns):
    columnas_faltantes = set(sklearn_columns) - set(csv_columns)
    columnas_extra = set(csv_columns) - set(sklearn_columns)
    print("❌ Vocabularios no coinciden.")
    if columnas_faltantes:
        print("Faltan en CSV:", columnas_faltantes)
    if columnas_extra:
        print("Extras en CSV:", columnas_extra)
else:
    # Reordenar columnas para que coincidan
    df_sklearn = df_sklearn[csv_columns]
    df_csv.index = etiquetas

    # Comparar valores
    iguales = (df_csv.values == df_sklearn.values).all()
    if iguales:
        print("✅ Las matrices son idénticas.")
    else:
        print("❌ Las matrices son diferentes. Mostrando diferencias...")

        # Mostrar diferencias con máscara booleana
        diferencias = df_csv != df_sklearn
        diferencias_localizadas = df_csv[diferencias]
        print(diferencias_localizadas.stack().head())

        # Exportar diferencias si quieres revisarlas
        df_diferencias = df_csv.copy()
        df_diferencias[diferencias] = "ERROR"
        df_diferencias.to_csv("diferencias_vs_sklearn.csv", index=False)
        print("Diferencias guardadas en 'diferencias_vs_sklearn.csv'")


✅ Las matrices son idénticas.


# Verificacion de resultado: serial vs paralelo

In [ ]:
df_paralelo = pd.read_csv("bolsa_paralelo.csv")
print("📥 CSV paralelo cargado con forma:", df_paralelo.shape)

# Leer archivo correcto
df_esperado = pd.read_csv("bolsa_serial.csv")
df_esperado.index = etiquetas
print("📥 CSV esperado cargado con forma:", df_esperado.shape)

# Verificar vocabulario
if set(df_esperado.columns) != set(df_paralelo.columns):
    print("❌ Vocabularios no coinciden.")
    print("Faltan:", set(df_esperado.columns) - set(df_paralelo.columns))
    print("Extras:", set(df_paralelo.columns) - set(df_esperado.columns))
else:
    print("✅ Vocabularios coinciden.")
    # Reordenar columnas
    df_paralelo = df_paralelo[df_esperado.columns]

    # Verificar filas sin importar orden
    valores_esperados = df_esperado.values
    valores_paralelo = df_paralelo.values.tolist()

    fila_faltante = False
    for fila in valores_esperados:
        if list(fila) not in valores_paralelo:
            fila_faltante = True
            print("❌ Fila no encontrada en el CSV paralelo:")
            print(fila)
            break

    if not fila_faltante:
        print("✅ Todos los documentos están presentes en bolsa_paralelo.csv con los mismos conteos.")



📥 CSV paralelo cargado con forma: (6, 15164)
📥 CSV esperado cargado con forma: (6, 15164)
✅ Vocabularios coinciden.
✅ Todos los documentos están presentes en bolsa_paralelo.csv con los mismos conteos.


# Analisis de resultados de ejecucion

In [11]:
# Cargamos el csv de resultados
df_resultados = pd.read_csv("resultados.csv")

# Obtenemos los promedios de ejecucion correspondientes
prom_serial = df_resultados["tiempo_serial"].mean()
prom_paralelo = df_resultados["tiempo_paralelo"].mean()
print("Tiempo promedio serial:", prom_serial)
print("Tiempo promedio paralelo:", prom_paralelo)
print("Speedup:" , prom_serial / prom_paralelo)

Tiempo promedio serial: 0.11829886666666667
Tiempo promedio paralelo: 0.006078152333333334
Speedup: 19.462965088568307
